In [0]:
#Importing Spark Libraries 

import sys
import pyspark
from pyspark import SparkContext

import pyspark.sql
from pyspark.sql import SparkSession
from pyspark.sql import SQLContext
from pyspark.sql.dataframe import DataFrame
import pyspark.sql.types as T

import pyspark.sql.functions as F 
from pyspark.sql.functions import *
from pyspark.sql.functions import col
from pyspark.sql.functions import isnan,when,count
from pyspark.sql.functions import ceil, col
from pyspark.sql.window import Window

print("Loaded Libraries Successfully")

Loaded Libraries Successfully

In [0]:
#Initialise Spark Session and Instance 

spark=SparkSession.builder.master('local').appName('Auto Analysis').enableHiveSupport().getOrCreate()

sc=SparkContext.getOrCreate()

sqlContext=SQLContext(spark)

print("Initialised Session and Cluster")

Initialised Session and Cluster

In [0]:
#Read Data - (CSV Format)

# File location and type
file_location = "/FileStore/tables/data.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df)
print("Loaded Data Successfully")

Make Model Year Engine Fuel Type Engine HP Engine Cylinders Transmission Type Driven_Wheels Number of Doors Market Category Vehicle Size Vehicle Style highway MPG city mpg Popularity MSRP BMW 1 Series M 2011 premium unleaded (required) 335 6 MANUAL rear wheel drive 2 Factory Tuner,Luxury,High-Performance Compact Coupe 26 19 3916 46135 BMW 1 Series 2011 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 28 19 3916 40650 BMW 1 Series 2011 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 36350 BMW 1 Series 2011 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 18 3916 29450 BMW 1 Series 2011 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 18 3916 34500 BMW 1 Series 2012 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 18 3916 31200 BMW 1 Series 2012 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 26 17 3916 44100 BMW 1 Series 2012 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 39300 BMW 1 Series 2012 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 18 3916 36900 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 27 18 3916 37200 BMW 1 Series 2013 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 39600 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 19 3916 31500 BMW 1 Series 2013 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 28 19 3916 44400 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 19 3916 37200 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 19 3916 31500 BMW 1 Series 2013 premium unleaded (required) 320 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Convertible 25 18 3916 48250 BMW 1 Series 2013 premium unleaded (required) 320 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 43550 Audi 100 1992 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1992 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1992 regular unleaded 172 6 AUTOMATIC all wheel drive 4 Luxury Midsize Wagon 20 16 3105 2000 Audi 100 1992 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1992 regular unleaded 172 6 MANUAL all wheel drive 4 Luxury Midsize Sedan 21 16 3105 2000 Audi 100 1993 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1993 regular unleaded 172 6 AUTOMATIC all wheel drive 4 Luxury Midsize Wagon 20 16 3105 2000 Audi 100 1993 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1993 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1993 regular unleaded 172 6 MANUAL all wheel drive 4 Luxury Midsize Sedan 21 16 3105 2000 Audi 100 1994 regular unleaded 172 6 AUTOMATIC front wheel drive 4 Luxury Midsize Wagon 21 16 3105 2000 Audi 100 1994 regular unleaded 172 6 MANUAL all wheel drive 4 Luxury Midsize Sedan 22 16 3105 2000 Audi 100 1994 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 22 17 3105 2000 Audi 100 1994 regular unleaded 172 6 AUTOMATIC front wheel drive 4 Luxury Midsize Sedan 22 16 3105 2000 Audi 100 1994 regular unleaded 172 6 AUTOMATIC all wheel drive 4 Luxury Midsize Wagon 21 16 3105 2000 FIAT 124 Spider 2017 premium unleaded (recommended) 160 4 MANUAL rear wh

Loaded Data Successfully

In [0]:
#Rename Columns 

df= df.withColumnRenamed("Make","Brand")\
      .withColumnRenamed("Engine Fuel Type","Fuel_Type")\
      .withColumnRenamed("Engine HP","Horsepower")\
      .withColumnRenamed("Engine Cylinders","Cylinders")\
      .withColumnRenamed("Transmission Type","Transmission")\
      .withColumnRenamed("Driven_Wheels","Drive_Type")\
      .withColumnRenamed("Number of Doors","Doors")\
      .withColumnRenamed("Market Category","Category")\
      .withColumnRenamed("Vehicle Size","Size")\
      .withColumnRenamed("Vehicle Style","Style")\
      .withColumnRenamed("highway MPG","MPG_Highway")\
      .withColumnRenamed("city mpg","MPG_City")\
      .withColumnRenamed("MSRP","Price")

df.printSchema()

root
-- Brand: string (nullable = true)
-- Model: string (nullable = true)
-- Year: integer (nullable = true)
-- Fuel_Type: string (nullable = true)
-- Horsepower: integer (nullable = true)
-- Cylinders: integer (nullable = true)
-- Transmission: string (nullable = true)
-- Drive_Type: string (nullable = true)
-- Doors: integer (nullable = true)
-- Category: string (nullable = true)
-- Size: string (nullable = true)
-- Style: string (nullable = true)
-- MPG_Highway: integer (nullable = true)
-- MPG_City: integer (nullable = true)
-- Popularity: integer (nullable = true)
-- Price: integer (nullable = true)

In [0]:
#Display Dataset
display(df)

Brand Model Year Fuel_Type Horsepower Cylinders Transmission Drive_Type Doors Category Size Style MPG_Highway MPG_City Popularity Price BMW 1 Series M 2011 premium unleaded (required) 335 6 MANUAL rear wheel drive 2 Factory Tuner,Luxury,High-Performance Compact Coupe 26 19 3916 46135 BMW 1 Series 2011 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 28 19 3916 40650 BMW 1 Series 2011 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 36350 BMW 1 Series 2011 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 18 3916 29450 BMW 1 Series 2011 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 18 3916 34500 BMW 1 Series 2012 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 18 3916 31200 BMW 1 Series 2012 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 26 17 3916 44100 BMW 1 Series 2012 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 39300 BMW 1 Series 2012 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 18 3916 36900 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 27 18 3916 37200 BMW 1 Series 2013 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 39600 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 19 3916 31500 BMW 1 Series 2013 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 28 19 3916 44400 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 19 3916 37200 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 19 3916 31500 BMW 1 Series 2013 premium unleaded (required) 320 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Convertible 25 18 3916 48250 BMW 1 Series 2013 premium unleaded (required) 320 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 43550 Audi 100 1992 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1992 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1992 regular unleaded 172 6 AUTOMATIC all wheel drive 4 Luxury Midsize Wagon 20 16 3105 2000 Audi 100 1992 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1992 regular unleaded 172 6 MANUAL all wheel drive 4 Luxury Midsize Sedan 21 16 3105 2000 Audi 100 1993 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1993 regular unleaded 172 6 AUTOMATIC all wheel drive 4 Luxury Midsize Wagon 20 16 3105 2000 Audi 100 1993 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1993 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1993 regular unleaded 172 6 MANUAL all wheel drive 4 Luxury Midsize Sedan 21 16 3105 2000 Audi 100 1994 regular unleaded 172 6 AUTOMATIC front wheel drive 4 Luxury Midsize Wagon 21 16 3105 2000 Audi 100 1994 regular unleaded 172 6 MANUAL all wheel drive 4 Luxury Midsize Sedan 22 16 3105 2000 Audi 100 1994 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 22 17 3105 2000 Audi 100 1994 regular unleaded 172 6 AUTOMATIC front wheel drive 4 Luxury Midsize Sedan 22 16 3105 2000 Audi 100 1994 regular unleaded 172 6 AUTOMATIC all wheel drive 4 Luxury Midsize Wagon 21 16 3105 2000 FIAT 124 Spider 2017 premium unleaded (recommended) 160 4 MANUAL rear wheel drive 2 Performance Compact Convertible 35 26 81

In [0]:
#Show DS as Pandas Dataframe 
df.toPandas()

Out[282]:

Brand 
 Model 
 Year 
 Fuel_Type 
 Horsepower 
 Cylinders 
 Transmission 
 Drive_Type 
 Doors 
 Category 
 Size 
 Style 
 MPG_Highway 
 MPG_City 
 Popularity 
 Price 
 
 
 
 
 0 
 BMW 
 1 Series M 
 2011 
 premium unleaded (required) 
 335.0 
 6.0 
 MANUAL 
 rear wheel drive 
 2.0 
 Factory Tuner,Luxury,High-Performance 
 Compact 
 Coupe 
 26 
 19 
 3916 
 46135 
 
 
 1 
 BMW 
 1 Series 
 2011 
 premium unleaded (required) 
 300.0 
 6.0 
 MANUAL 
 rear wheel drive 
 2.0 
 Luxury,Performance 
 Compact 
 Convertible 
 28 
 19 
 3916 
 40650 
 
 
 2 
 BMW 
 1 Series 
 2011 
 premium unleaded (required) 
 300.0 
 6.0 
 MANUAL 
 rear wheel drive 
 2.0 
 Luxury,High-Performance 
 Compact 
 Coupe 
 28 
 20 
 3916 
 36350 
 
 
 3 
 BMW 
 1 Series 
 2011 
 premium unleaded (required) 
 230.0 
 6.0 
 MANUAL 
 rear wheel drive 
 2.0 
 Luxury,Performance 
 Compact 
 Coupe 
 28 
 18 
 3916 
 29450 
 
 
 4 
 BMW 
 1 Series 
 2011 
 premium unleaded (required) 
 230.0 
 6.0 
 MANUAL 
 rear wheel drive 
 2.0 
 Luxury 
 Compact 
 Convertible 
 28 
 18 
 3916 
 34500 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 
 
 11909 
 Acura 
 ZDX 
 2012 
 premium unleaded (required) 
 300.0 
 6.0 
 AUTOMATIC 
 all wheel drive 
 4.0 
 Crossover,Hatchback,Luxury 
 Midsize 
 4dr Hatchback 
 23 
 16 
 204 
 46120 
 
 
 11910 
 Acura 
 ZDX 
 2012 
 premium unleaded (required) 
 300.0 
 6.0 
 AUTOMATIC 
 all wheel drive 
 4.0 
 Crossover,Hatchback,Luxury 
 Midsize 
 4dr Hatchback 
 23 
 16 
 204 
 56670 
 
 
 11911 
 Acura 
 ZDX 
 2012 
 premium unleaded (required) 
 300.0 
 6.0 
 AUTOMATIC 
 all wheel drive 
 4.0 
 Crossover,Hatchback,Luxury 
 Midsize 
 4dr Hatchback 
 23 
 16 
 204 
 50620 
 
 
 11912 
 Acura 
 ZDX 
 2013 
 premium unleaded (recommended) 
 300.0 
 6.0 
 AUTOMATIC 
 all wheel drive 
 4.0 
 Crossover,Hatchback,Luxury 
 Midsize 
 4dr Hatchback 
 23 
 16 
 204 
 50920 
 
 
 11913 
 Lincoln 
 Zephyr 
 2006 
 regular unleaded 
 221.0 
 6.0 
 AUTOMATIC 
 front wheel drive 
 4.0 
 Luxury 
 Midsize 
 Sedan 
 26 
 17 
 61 
 28995 
 
 
 
 11914 rows × 16 columns

In [0]:
#Eager Evaluation
spark.conf.set("spark.sql.repl.eagerEval.enabled", True)

In [0]:
#Dataset Details
print("The Columns in the Dataset are:",df.columns)

The Columns in the Dataset are: ['Brand', 'Model', 'Year', 'Fuel_Type', 'Horsepower', 'Cylinders', 'Transmission', 'Drive_Type', 'Doors', 'Category', 'Size', 'Style', 'MPG_Highway', 'MPG_City', 'Popularity', 'Price']

In [0]:
print("The Dataset has",df.count(),"entries and",len(df.columns),"columns.")

The Dataset has 11914 entries and 16 columns.

In [0]:
#Statistical Insights 
display(df.describe())

summary Brand Model Year Fuel_Type Horsepower Cylinders Transmission Drive_Type Doors Category Size Style MPG_Highway MPG_City Popularity Price count 11914 11914 11914 11911 11845 11884 11914 11914 11908 11914 11914 11914 11914 11914 11914 11914 mean null 745.5822222222222 2010.384337753903 null 249.38607007176023 5.628828677213059 null null 3.4360933825999327 null null null 26.637485311398354 19.73325499412456 1554.9111969111968 40594.737032063116 stddev null 1490.8280590623795 7.5797398875957995 null 109.19187025917194 1.78055934824622 null null 0.8813153865835529 null null null 8.863000766979422 8.987798160299237 1441.8553466274648 60109.10360365422 min Acura 1 Series 1990 diesel 55 0 AUTOMATED_MANUAL all wheel drive 2 Crossover Compact 2dr Hatchback 12 7 2 2000 max Volvo xD 2017 regular unleaded 1001 16 UNKNOWN rear wheel drive 4 Performance,Hybrid Midsize Wagon 354 137 5657 2065902

In [0]:
# Drop Duplicates - If Present 

df.dropDuplicates()

Out[287]:

Brand Model Year Fuel_Type Horsepower Cylinders Transmission Drive_Type Doors Category Size Style MPG_Highway MPG_City Popularity Price 
 Audi 100 1992 regular unleaded 172 6 AUTOMATIC all wheel drive 4 Luxury Midsize Wagon 20 16 3105 2000 
 BMW 1 Series 2013 premium unleaded ... 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 19 3916 37200 
 Audi 100 1993 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 
 Audi 100 1993 regular unleaded 172 6 AUTOMATIC all wheel drive 4 Luxury Midsize Wagon 20 16 3105 2000 
 BMW 1 Series 2011 premium unleaded ... 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 18 3916 34500 
 Audi 100 1992 regular unleaded 172 6 MANUAL all wheel drive 4 Luxury Midsize Sedan 21 16 3105 2000 
 BMW 1 Series 2013 premium unleaded ... 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 27 18 3916 37200 
 BMW 1 Series 2011 premium unleaded ... 300 6 MANUAL rear wheel drive 2 Luxury,High-Perfo... Compact Coupe 28 20 3916 36350 
 BMW 1 Series 2013 premium unleaded ... 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 19 3916 31500 
 BMW 1 Series 2011 premium unleaded ... 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 28 19 3916 40650 
 Audi 100 1992 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 
 BMW 1 Series 2013 premium unleaded ... 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 28 19 3916 44400 
 BMW 1 Series M 2011 premium unleaded ... 335 6 MANUAL rear wheel drive 2 Factory Tuner,Lux... Compact Coupe 26 19 3916 46135 
 BMW 1 Series 2013 premium unleaded ... 320 6 MANUAL rear wheel drive 2 Luxury,High-Perfo... Compact Coupe 28 20 3916 43550 
 BMW 1 Series 2012 premium unleaded ... 300 6 MANUAL rear wheel drive 2 Luxury,High-Perfo... Compact Coupe 28 20 3916 39300 
 BMW 1 Series 2012 premium unleaded ... 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 18 3916 36900 
 BMW 1 Series 2012 premium unleaded ... 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 18 3916 31200 
 BMW 1 Series 2012 premium unleaded ... 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 26 17 3916 44100 
 BMW 1 Series 2011 premium unleaded ... 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 18 3916 29450 
 BMW 1 Series 2013 premium unleaded ... 300 6 MANUAL rear wheel drive 2 Luxury,High-Perfo... Compact Coupe 28 20 3916 39600 
 
only showing top 20 rows

In [0]:
#Remove NaN, Missing Values - using where clause

df=df.where("Category!='N/A'")

df=df.where("Transmission!='UNKNOWN'")

display(df)

Brand Model Year Fuel_Type Horsepower Cylinders Transmission Drive_Type Doors Category Size Style MPG_Highway MPG_City Popularity Price BMW 1 Series M 2011 premium unleaded (required) 335 6 MANUAL rear wheel drive 2 Factory Tuner,Luxury,High-Performance Compact Coupe 26 19 3916 46135 BMW 1 Series 2011 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 28 19 3916 40650 BMW 1 Series 2011 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 36350 BMW 1 Series 2011 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 18 3916 29450 BMW 1 Series 2011 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 18 3916 34500 BMW 1 Series 2012 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 18 3916 31200 BMW 1 Series 2012 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 26 17 3916 44100 BMW 1 Series 2012 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 39300 BMW 1 Series 2012 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 18 3916 36900 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 27 18 3916 37200 BMW 1 Series 2013 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 39600 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 19 3916 31500 BMW 1 Series 2013 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 28 19 3916 44400 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 19 3916 37200 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 19 3916 31500 BMW 1 Series 2013 premium unleaded (required) 320 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Convertible 25 18 3916 48250 BMW 1 Series 2013 premium unleaded (required) 320 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 43550 Audi 100 1992 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1992 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1992 regular unleaded 172 6 AUTOMATIC all wheel drive 4 Luxury Midsize Wagon 20 16 3105 2000 Audi 100 1992 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1992 regular unleaded 172 6 MANUAL all wheel drive 4 Luxury Midsize Sedan 21 16 3105 2000 Audi 100 1993 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1993 regular unleaded 172 6 AUTOMATIC all wheel drive 4 Luxury Midsize Wagon 20 16 3105 2000 Audi 100 1993 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1993 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1993 regular unleaded 172 6 MANUAL all wheel drive 4 Luxury Midsize Sedan 21 16 3105 2000 Audi 100 1994 regular unleaded 172 6 AUTOMATIC front wheel drive 4 Luxury Midsize Wagon 21 16 3105 2000 Audi 100 1994 regular unleaded 172 6 MANUAL all wheel drive 4 Luxury Midsize Sedan 22 16 3105 2000 Audi 100 1994 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 22 17 3105 2000 Audi 100 1994 regular unleaded 172 6 AUTOMATIC front wheel drive 4 Luxury Midsize Sedan 22 16 3105 2000 Audi 100 1994 regular unleaded 172 6 AUTOMATIC all wheel drive 4 Luxury Midsize Wagon 21 16 3105 2000 FIAT 124 Spider 2017 premium unleaded (recommended) 160 4 MANUAL rear wheel drive 2 Performance Compact Convertible 35 26 81

In [0]:
#Getting Count of NaN, Missing Values in Dataframe 

display(df.select([count(when(isnan(c), c)).alias(c) for c in df.columns]))

Brand Model Year Fuel_Type Horsepower Cylinders Transmission Drive_Type Doors Category Size Style MPG_Highway MPG_City Popularity Price 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0

In [0]:
# Selecting Data and Distinct Values - Categorical Data

display(df.select('Brand').distinct())

display(df.select('Model').distinct())

display(df.select('Fuel_Type').distinct())

display(df.select('Cylinders').distinct())

display(df.select('Transmission').distinct())

display(df.select('Drive_Type').distinct()) 

display(df.select('Category').distinct())

display(df.select('Size').distinct())

display(df.select('Style').distinct())

Brand Volkswagen Oldsmobile Infiniti Lexus FIAT Maserati Rolls-Royce Scion Mitsubishi Kia Chevrolet Volvo Hyundai Saab Honda Audi Lamborghini Cadillac Plymouth Genesis Pontiac Land Rover Alfa Romeo Mercedes-Benz McLaren Chrysler Lincoln Tesla BMW Suzuki Acura HUMMER Ferrari GMC Buick Porsche Spyker Lotus Bentley Toyota Aston Martin Dodge Nissan Mazda Maybach Ford Subaru Bugatti

Model G Convertible MDX RS 7 944 California T GLE-Class S60 TC Highlander Hybrid Shadow XLR-V 740 Captiva Sport DBS Mark VII Q7 MR2 Silver Seraph G Sedan Gallardo Omni 940 Camry ES 300 HHR Shelby GT500 Spark EV allroad quattro Mazdaspeed Protege 200 GL-Class Mazdaspeed 6 Veyron 16.4 XTS Alpina Elise Juke MP4-12C Santa Fe Sport Seville Sonoma STS-V Tribute Hybrid 323 CLK-Class Elantra Touring Outback 300M Corrado e-Golf Tiburon i3 IS 250 C R8 Uplander Venza Z4 A6 Golf J30 Q50 QX4 Solstice Forester FX50 2 Series 3 4 Series Gran Coupe Avalanche Continental GTC Flex Sixty Special Yukon Evora 400 Expo M4 Nitro 575M Focus Optima RC F Veracruz 3 Series Express Cargo NX 300h RX 330 F430 Supra Titan EX G Coupe Ghibli M45 Taurus X Durango F-150 Sundance Vanquish 9-7X Freelander NX Phantom Drophead Coupe Q60 Coupe Prius S60 Cross Country S6 Aveo H3 LS 400 Cruze Dawn K900 S8 Tribeca A8 Fusion I35 SC 430 Town Car ATS-V Ghost Series II QX50 Impreza Model S MX-5 Miata S7 Stealth Wraith Forte Neon 9-3 Griffin Impreza WRX Firebird IS 250 NSX Range Rover Evoque 9-3 Justy Rogue Select Jetta GLI X4 Mulsanne Tundra Z8 190-Class 928 Continental Element Pathfinder Sorento CX-7 RAV4 Hybrid Brooklands Freestyle IS F Malibu V90 850 Azure T Outlander Cobalt LX 570 X6 Black Diamond Avalanche BRZ Discovery Sport ILX Navigator Terraza I30 Stratus Taurus 300 300ZX E-Series Van Grand Caravan M6 F-150 SVT Lightning FF Ghost S4 Vibe Yukon Denali Journey MKS 100 3000GT Aurora Azure Bolt EV C-Class S80 Sierra 1500 Typhoon V60 Integra Metris Sebring FX35 Lucerne RC 200t Blackwood Legacy Mazdaspeed 3 RS 5 420-Class SC 400 Tahoe Hybrid ES 250 GS 350 S90 SLS AMG Accord CL TSX Sport Wagon C-Max Hybrid Discovery GS 400 Phantom Coupe Prius Prime SRX 5 Series Gran Turismo Escalade ESV MKZ Hybrid Camry Hybrid LR4 Rapide S XC60 ActiveHybrid X6 Arnage GT-R Tribute X1 Continental Supersports CTS-V Coupe Crosstrek Supersports Convertible ISR ALPINA B6 Gran Coupe HS 250h tC CTS-V Evora Fit Highlander Leaf RS 6 Civic CRX Mark LT M Murano S3 Rogue Verano Mark VIII Optima Hybrid SLK-Class CT6 Focus RS GX 460 MKC RX 400h B9 Tribeca Mustang Panamera Prius v SSR Bonneville 4C Armada GT New Beetle Prelude V12 Vantage S Continental Supersports Convertible Grand Voyager Q5 458 Italia Carrera GT Defender S-10 400-Class Yukon Hybrid Spyder ES 330 GLA-Class Silverado 1500 Classic SLC-Class 3 Series Gran Turismo CLA-Class Esprit Genesis LR3 Torrent 500X 90 Allante CX-5 TSX Cayman Touareg 2 C30 Savana B-Series Pickup Silverado 1500 Hybrid V12 Vanquish 200SX 9-5 Eldorado 240SX Discovery Series II Fusion Hybrid Terrain 7 Series Golf Alltrack xD 500e 9-2X Lancer Evolution Park Ward RS 4 Fleetwood IS 200t Range Rover Azera CLS-Class CTS Wagon FX45 iM Q40 Accord Crosstour Escalade EXT FX Precis S70 Touareg Yukon XL G6 M4 GTS R-Class Regal SLS AMG GT Final Edition G37 QX80 Suburban Swift Aspire M35 Outlander Sport RX 300 RX-8 Contour SVT Tiguan X3 ILX Hybrid RSX SLX Town and Country V8 Vantage Celica Jetta Hybrid CT 200h Sonata Versa Note G80 MKZ MR2 Spyder Daytona Murano CrossCabriolet Santa Fe AMG GT NX 200t Sierra 1500 Hybrid CC Eclipse Spyder Reno Avalon Camaro Fiesta G3 Laser LHS Phaeton 570S Escalade Hybrid iQ 9000 Genesis Coupe GTI M37 TL V70 Charger Envision Routan Continental GT3-R ES 350 Insight V50 X5 M 5 Series A4 allroad GS F Horizon 968 C36 AMG Crossfire Reventon ZDX 86 Enzo Grand Vitara Matrix Silverado 1500 Acadia Limited i-MiEV LR2 H3T 350-Class 350Z 360 600-Class Pacifica SX4 XC Escape G-Class Golf SportWagen M5 M6 Gran Coupe S40 Civic del Sol Civic Sierra 1500 Classic Continental Flying Spur Continental GT Speed Convertible CR-V G20 IS 350 Quattroporte TrailBlazer Cabriolet Escalade GS 300 Syclone XLR 370Z Fit EV LS 600h L Mazdaspeed MX-5 Miata RX-7 Virage xA E-Class Elantra GT Express Q45 Z3 ATS Coupe DB7 MKT Flying Spur Golf R Impala Maxima GLI Lancer QX56 XT5 Aspen CL-Class LX 470 RDX Transit Wagon 500 Concorde DTS LS 460 240 Explorer Altima Hybrid Beetle RL DB9 Explorer Sp

Fuel_Type premium unleaded (required) flex-fuel (unleaded/natural gas) flex-fuel (unleaded/E85) diesel flex-fuel (premium unleaded required/E85) flex-fuel (premium unleaded recommended/E85) premium unleaded (recommended) electric regular unleaded

Cylinders 12 null 6 16 3 5 4 8 10 0

Transmission MANUAL AUTOMATIC AUTOMATED_MANUAL DIRECT_DRIVE

Drive_Type four wheel drive rear wheel drive all wheel drive front wheel drive

Category Crossover,Flex Fuel,Performance Crossover,Exotic,Luxury,High-Performance Hatchback,Factory Tuner,Luxury,Performance Crossover,Hatchback,Performance Exotic,Flex Fuel,Luxury,High-Performance Hatchback Crossover,Hatchback,Factory Tuner,Performance Factory Tuner,Luxury,High-Performance Hatchback,Diesel Crossover,Hybrid Crossover Crossover,Factory Tuner,Luxury,Performance Hatchback,Luxury,Performance Diesel,Luxury Crossover,Diesel Diesel Flex Fuel,Diesel Luxury,Performance,Hybrid Exotic,Factory Tuner,Luxury,High-Performance Hatchback,Hybrid Crossover,Luxury,High-Performance Crossover,Flex Fuel,Luxury,Performance Exotic,Performance Crossover,Luxury,Performance,Hybrid Flex Fuel,Hybrid Exotic,Flex Fuel,Factory Tuner,Luxury,High-Performance Flex Fuel,Luxury,High-Performance Hatchback,Luxury Hybrid Performance,Hybrid Exotic,Luxury Flex Fuel,Luxury Luxury,Hybrid Flex Fuel Luxury,High-Performance Crossover,Factory Tuner,Performance Crossover,Hatchback Crossover,Exotic,Luxury,Performance Crossover,Hatchback,Luxury Factory Tuner,Luxury,Performance Exotic,High-Performance Exotic,Luxury,High-Performance Crossover,Flex Fuel,Luxury Luxury,Performance Factory Tuner,Luxury Exotic,Luxury,High-Performance,Hybrid Flex Fuel,Performance,Hybrid Flex Fuel,Factory Tuner,Luxury,High-Performance Crossover,Luxury,Hybrid Hatchback,Luxury,Hybrid Crossover,Performance Crossover,Luxury Crossover,Flex Fuel Hatchback,Performance Luxury Luxury,High-Performance,Hybrid Hatchback,Flex Fuel Hatchback,Factory Tuner,Performance Performance High-Performance Exotic,Factory Tuner,Luxury,Performance Exotic,Factory Tuner,High-Performance Crossover,Luxury,Performance Factory Tuner,High-Performance Flex Fuel,Luxury,Performance Flex Fuel,Performance Crossover,Factory Tuner,Luxury,High-Performance Exotic,Luxury,Performance Factory Tuner,Performance Crossover,Luxury,Diesel Hatchback,Factory Tuner,High-Performance

Size Compact Midsize Large

Style 2dr Hatchback Convertible Cargo Van Passenger Van Sedan Passenger Minivan Convertible SUV Extended Cab Pickup 4dr SUV Wagon 2dr SUV Crew Cab Pickup Cargo Minivan Regular Cab Pickup 4dr Hatchback Coupe

In [0]:
#Get Insights via Aggregating Data - Numerical

max_hp= df.agg({'Horsepower':'max'}).show()
min_hp= df.agg({'Horsepower':'min'}).show()

mpg_highway=df.agg({'MPG_Highway':'max'}).show()
mpg_highway_min=df.agg({'MPG_Highway':'min'}).show()

mpg_city=df.agg({'MPG_City':'max'}).show()
mpg_city_min=df.agg({'MPG_City':'min'}).show()

+---------------+
max(Horsepower)|
+---------------+
 1001|
+---------------+

+---------------+
min(Horsepower)|
+---------------+
 55|
+---------------+

+----------------+
max(MPG_Highway)|
+----------------+
 354|
+----------------+

+----------------+
min(MPG_Highway)|
+----------------+
 12|
+----------------+

+-------------+
max(MPG_City)|
+-------------+
 137|
+-------------+

+-------------+
min(MPG_City)|
+-------------+
 7|
+-------------+

In [0]:
price_max=df.agg({'Price':'max'}).show()
price_min=df.agg({'Price':'min'}).show()

+----------+
max(Price)|
+----------+
 2065902|
+----------+

+----------+
min(Price)|
+----------+
 2000|
+----------+

In [0]:
#Ordering Data

display(df.select('Brand','Model','Horsepower').orderBy('Year',ascending=True))

Brand Model Horsepower Infiniti M30 162 Mercedes-Benz 560-Class 238 Volvo 760 162 Lincoln Mark VII 225 Audi 200 162 Lincoln Mark VII 225 Volvo 760 162 Dodge Omni 93 Buick Reatta 165 Mercedes-Benz 350-Class 134 Volvo 780 188 Chrysler TC 141 Chrysler TC 200 Volvo 740 114 Volvo 780 144 Audi 80 108 Mercedes-Benz 350-Class 134 Volvo 740 153 Audi 80 130 Audi 200 162 Porsche 944 208 Volvo 740 114 Porsche 944 208 Cadillac Brougham 140 Mercedes-Benz 420-Class 201 Volvo 740 114 Cadillac Brougham 140 Audi 200 162 Honda Civic CRX 62 Volvo 740 114 Honda Civic CRX 108 Honda Civic CRX 92 Mercedes-Benz 560-Class 238 Volvo 740 153 Audi Coupe 164 Lexus ES 250 156 Volvo 760 144 Plymouth Horizon 93 Volvo 740 162 Mercedes-Benz 190-Class 158 Volvo 740 162 Volvo 740 162 Volvo 740 114 Volvo 740 162 Volvo 740 114 Audi 80 130 Audi 80 130 Porsche 944 208 Cadillac Allante 200 Porsche 944 208 Cadillac Brougham 170 Honda Civic CRX 108 Honda Civic CRX 92 Honda Civic CRX 62 Audi Coupe 164 Volvo Coupe 188 Dodge Daytona 152 Dodge Daytona 152 Audi 200 217 Audi 200 217 Dodge Daytona 152 Dodge Daytona 100 Audi 200 162 Dodge Daytona 141 Dodge Daytona 100 Lexus ES 250 156 Ford Festiva 63 Volvo 240 114 Ford Festiva 63 Infiniti M30 162 Volvo 240 114 Infiniti M30 162 Lincoln Mark VII 225 Volvo 240 114 Lincoln Mark VII 225 Nissan NX 140 Nissan NX 110 Mercedes-Benz 300-Class 177 Buick Reatta 170 Mercedes-Benz 300-Class 158 Chrysler TC 141 Mercedes-Benz 300-Class 177 GMC Syclone 280 Mercedes-Benz 300-Class 177 Mercedes-Benz 300-Class 177 Mercedes-Benz 190-Class 130 Mercedes-Benz 300-Class 177 Mercedes-Benz 300-Class 177 Mercedes-Benz 300-Class 228 Mercedes-Benz 300-Class 217 Mercedes-Benz 350-Class 134 Mercedes-Benz 300-Class 121 Mercedes-Benz 350-Class 134 Mercedes-Benz 420-Class 201 Mercedes-Benz 500-Class 322 Mercedes-Benz 560-Class 238 Mercedes-Benz 560-Class 238 Volvo 740 114 Volvo 740 162 Volvo 740 114 Audi 80 130 Audi 80 130 Cadillac Allante 200 Cadillac Brougham 170 Dodge Colt 92 Dodge Colt 92 Plymouth Colt 92 Plymouth Colt 92 Volkswagen Corrado 158 Volkswagen Corrado 178 Dodge Daytona 224 Dodge Daytona 141 Dodge Daytona 100 Dodge Daytona 100 Ford Festiva 63 Hyundai Excel 81 Hyundai Excel 81 Ford Festiva 63 Subaru Justy 73 Subaru Justy 73 Subaru Justy 66 Subaru Justy 73 Plymouth Laser 135 Plymouth Laser 92 Plymouth Laser 195 Plymouth Laser 195 Infiniti M30 162 Infiniti M30 162 Lincoln Mark VII 225 Lincoln Mark VII 225 Dodge Shadow 93 Nissan NX 140 Mitsubishi Precis 81 Dodge Shadow 152 Dodge Shadow 93 Dodge Shadow 93 Dodge Shadow 152 Dodge Shadow 100 Dodge Shadow 93 Dodge Shadow 152 Dodge Shadow 152 Dodge Shadow 100 Plymouth Sundance 100 Plymouth Sundance 93 Plymouth Sundance 93 Plymouth Sundance 93 Plymouth Sundance 100 GMC Typhoon 285 Plymouth Sundance 93 Acura Vigor 176 Audi V8 276 Acura Vigor 176 Audi 100 172 Volvo 740 114 Nissan NX 110 Audi 100 172 Audi 100 172 Audi 100 172 Audi 100 172 Mercedes-Benz 190-Class 158 Volvo 240 114 Mercedes-Benz 190-Class 130 Volvo 240 114 Volvo 240 114 Mercedes-Benz 300-Class 121 Mercedes-Benz 300-Class 228 Mercedes-Benz 300-Class 228 Mercedes-Benz 300-Class 177 Mercedes-Benz 300-Class 177 Mercedes-Benz 300-Class 177 Mercedes-Benz 300-Class 217 Mercedes-Benz 300-Class 148 Mercedes-Benz 300-Class 177 Mercedes-Benz 300-Class 158 Mazda 323 82 Mazda 323 82 Mercedes-Benz 400-Class 282 Mercedes-Benz 400-Class 268 Mercedes-Benz 500-Class 322 Mercedes-Benz 500-Class 322 Mercedes-Benz 500-Class 322 Mercedes-Benz 600-Class 402 Acura Legend 200 Mazda MX-3 130 Nissan NX 110 Dodge Shadow 100 Plymouth Sundance 93 Acura Vigor 176 Audi 100 172 Audi 100 172 Mercedes-Benz 300-Class 217 Cadillac Allante 295 Acura Legend 200 Acura Legend 230 Acura Legend 230 Toyota MR2 135 Toyota MR2 200 Nissan NX 140 Mazda RX-7 255 Dodge Shadow 93 Dodge Shadow 93 Dodge Shadow 100 Cadillac Sixty Special 200 Plymouth Sundance 100 Plymouth Sundance 100 Plymouth Sundance 93 GMC Typhoon 285 Audi 100 172 Acura Vigor 176 Audi V8 276 Mazda MX-3 130 Mazda MX-3 88 Audi 100 

In [0]:
#Filtering Data - Queries 

#1. Find % of People Using Honda with Automatic Transmission, and category under Luxury,Performance.

car_count=df.count()
honda_count=df.filter("Brand='Honda'").filter("Transmission='AUTOMATIC' or Category='Luxury,Performance'").count()

print("1.","People Using Honda Cars with Automatic Transmission and come under Luxury,Performance is",honda_count*100/car_count,"%")

#2. % Of People Using Electric Cars 

electric_count=df.filter("Fuel_Type='electric'").count()

print("2.",electric_count*100/car_count,"% of People use Electric cars.")

#3. Find Out Car and Model that comes under Electric 

model_electric=df.select('Brand','Model','Year').filter("Fuel_Type='electric'")
display(model_electric)

#4. Conditional Filtering 

display(df.filter("Brand='BMW'")\
  .filter("Fuel_Type='premium unleaded (required)' or Transmission='AUTOMATIC'")\
  .filter("Horsepower>500 or Price>85000"))

1. People Using Honda Cars with Automatic Transmission and come under Luxury,Performance is 2.7420736932305054 %
2. 0.7467254253886645 % of People use Electric cars.

Brand Model Year FIAT 500e 2015 FIAT 500e 2016 FIAT 500e 2017 Mercedes-Benz B-Class Electric Drive 2015 Mercedes-Benz B-Class Electric Drive 2016 Mercedes-Benz B-Class Electric Drive 2017 Chevrolet Bolt EV 2017 Chevrolet Bolt EV 2017 Volkswagen e-Golf 2015 Volkswagen e-Golf 2015 Volkswagen e-Golf 2016 Volkswagen e-Golf 2016 Honda Fit EV 2013 Honda Fit EV 2014 Ford Focus 2015 Ford Focus 2016 Ford Focus 2017 Mitsubishi i-MiEV 2014 Mitsubishi i-MiEV 2016 Mitsubishi i-MiEV 2017 BMW i3 2015 BMW i3 2016 BMW i3 2017 BMW i3 2017 Nissan Leaf 2014 Nissan Leaf 2014 Nissan Leaf 2014 Nissan Leaf 2015 Nissan Leaf 2015 Nissan Leaf 2015 Nissan Leaf 2015 Nissan Leaf 2016 Nissan Leaf 2016 Nissan Leaf 2016 Tesla Model S 2014 Tesla Model S 2014 Tesla Model S 2014 Tesla Model S 2014 Tesla Model S 2015 Tesla Model S 2015 Tesla Model S 2015 Tesla Model S 2015 Tesla Model S 2015 Tesla Model S 2016 Tesla Model S 2016 Tesla Model S 2016 Tesla Model S 2016 Tesla Model S 2016 Tesla Model S 2016 Tesla Model S 2016 Tesla Model S 2016 Tesla Model S 2016 Toyota RAV4 EV 2012 Toyota RAV4 EV 2013 Toyota RAV4 EV 2014 Chevrolet Spark EV 2014 Chevrolet Spark EV 2014 Chevrolet Spark EV 2015 Chevrolet Spark EV 2015 Chevrolet Spark EV 2016 Chevrolet Spark EV 2016

Brand Model Year Fuel_Type Horsepower Cylinders Transmission Drive_Type Doors Category Size Style MPG_Highway MPG_City Popularity Price BMW 6 Series Gran Coupe 2015 premium unleaded (required) 445 8 AUTOMATIC all wheel drive 4 Luxury,High-Performance Large Sedan 24 16 3916 92600 BMW 6 Series Gran Coupe 2015 premium unleaded (required) 445 8 AUTOMATIC rear wheel drive 4 Luxury,High-Performance Large Sedan 25 17 3916 89600 BMW 6 Series Gran Coupe 2016 premium unleaded (required) 445 8 AUTOMATIC all wheel drive 4 Luxury,High-Performance Large Sedan 24 15 3916 93900 BMW 6 Series Gran Coupe 2016 premium unleaded (required) 445 8 AUTOMATIC rear wheel drive 4 Luxury,High-Performance Large Sedan 25 17 3916 90900 BMW 6 Series Gran Coupe 2017 premium unleaded (required) 445 8 AUTOMATIC rear wheel drive 4 Luxury,High-Performance Large Sedan 24 17 3916 91200 BMW 6 Series Gran Coupe 2017 premium unleaded (required) 445 8 AUTOMATIC all wheel drive 4 Luxury,High-Performance Large Sedan 24 15 3916 94200 BMW 6 Series 2015 premium unleaded (required) 445 8 AUTOMATIC rear wheel drive 2 Luxury,High-Performance Midsize Convertible 25 17 3916 94900 BMW 6 Series 2015 premium unleaded (required) 315 6 AUTOMATIC all wheel drive 2 Luxury,Performance Midsize Convertible 29 20 3916 86600 BMW 6 Series 2015 premium unleaded (required) 445 8 AUTOMATIC all wheel drive 2 Luxury,High-Performance Midsize Coupe 25 16 3916 90400 BMW 6 Series 2015 premium unleaded (required) 445 8 AUTOMATIC rear wheel drive 2 Luxury,High-Performance Midsize Coupe 25 17 3916 87400 BMW 6 Series 2015 premium unleaded (required) 445 8 AUTOMATIC all wheel drive 2 Luxury,High-Performance Midsize Convertible 24 16 3916 97900 BMW 6 Series 2016 premium unleaded (required) 315 6 AUTOMATIC all wheel drive 2 Luxury,Performance Midsize Convertible 29 20 3916 87800 BMW 6 Series 2016 premium unleaded (required) 445 8 AUTOMATIC all wheel drive 2 Luxury,High-Performance Midsize Convertible 24 15 3916 99200 BMW 6 Series 2016 premium unleaded (required) 445 8 AUTOMATIC rear wheel drive 2 Luxury,High-Performance Midsize Convertible 25 17 3916 96200 BMW 6 Series 2016 premium unleaded (required) 445 8 AUTOMATIC all wheel drive 2 Luxury,High-Performance Midsize Coupe 25 16 3916 91700 BMW 6 Series 2016 premium unleaded (required) 445 8 AUTOMATIC rear wheel drive 2 Luxury,High-Performance Midsize Coupe 25 17 3916 88700 BMW 6 Series 2017 premium unleaded (required) 445 8 AUTOMATIC all wheel drive 2 Luxury,High-Performance Midsize Coupe 24 16 3916 92000 BMW 6 Series 2017 premium unleaded (required) 445 8 AUTOMATIC rear wheel drive 2 Luxury,High-Performance Midsize Coupe 24 17 3916 89000 BMW 6 Series 2017 premium unleaded (required) 315 6 AUTOMATIC rear wheel drive 2 Luxury,Performance Midsize Convertible 29 20 3916 85100 BMW 6 Series 2017 premium unleaded (required) 315 6 AUTOMATIC all wheel drive 2 Luxury,Performance Midsize Convertible 28 19 3916 88100 BMW 6 Series 2017 premium unleaded (required) 445 8 AUTOMATIC rear wheel drive 2 Luxury,High-Performance Midsize Convertible 24 17 3916 96500 BMW 6 Series 2017 premium unleaded (required) 445 8 AUTOMATIC all wheel drive 2 Luxury,High-Performance Midsize Convertible 24 15 3916 99500 BMW 7 Series 2015 premium unleaded (required) 535 12 AUTOMATIC rear wheel drive 4 Luxury,High-Performance Large Sedan 20 13 3916 141200 BMW 7 Series 2015 premium unleaded (required) 445 8 AUTOMATIC rear wheel drive 4 Luxury,High-Performance Large Sedan 25 16 3916 91000 BMW 7 Series 2015 premium unleaded (required) 445 8 AUTOMATIC all wheel drive 4 Luxury,High-Performance Large Sedan 24 16 3916 94000 BMW 7 Series 2015 premium unleaded (required) 445 8 AUTOMATIC rear wheel drive 4 Luxury,High-Performance Large Sedan 25 17 3916 87300 BMW 7 Series 2015 premium unleaded (required) 445 8 AUTOMATIC all wheel drive 4 Luxury,High-Performance Large Sedan 24 16 3916 90300 BMW 7 Series 2016 premium unleaded (required) 445 8 AUTOMATIC rear wheel drive 4 Luxury,High-Performance Large Sedan 25 

In [0]:
#Filtering - String Operations 

#1. isin
brand_filter=df[df.Brand.isin('BMW','Audi','Mazda','Honda','Volvo')]
display(brand_filter)

#2. like
model_filter=df[df.Model.like('%350 Z')]
display(model_filter)

#3. startswith 
start=df.filter(df["Fuel_Type"].startswith("prem"))
display(start)

#4. endswith
end=df.filter(df["Style"].endswith("le"))
display(end)

#5. contains
contain=df.filter(df["Drive_Type"].contains("all wheel drive"))
display(contain)

Brand Model Year Fuel_Type Horsepower Cylinders Transmission Drive_Type Doors Category Size Style MPG_Highway MPG_City Popularity Price BMW 1 Series M 2011 premium unleaded (required) 335 6 MANUAL rear wheel drive 2 Factory Tuner,Luxury,High-Performance Compact Coupe 26 19 3916 46135 BMW 1 Series 2011 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 28 19 3916 40650 BMW 1 Series 2011 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 36350 BMW 1 Series 2011 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 18 3916 29450 BMW 1 Series 2011 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 18 3916 34500 BMW 1 Series 2012 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 18 3916 31200 BMW 1 Series 2012 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 26 17 3916 44100 BMW 1 Series 2012 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 39300 BMW 1 Series 2012 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 18 3916 36900 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 27 18 3916 37200 BMW 1 Series 2013 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 39600 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 19 3916 31500 BMW 1 Series 2013 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 28 19 3916 44400 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 19 3916 37200 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 19 3916 31500 BMW 1 Series 2013 premium unleaded (required) 320 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Convertible 25 18 3916 48250 BMW 1 Series 2013 premium unleaded (required) 320 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 43550 Audi 100 1992 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1992 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1992 regular unleaded 172 6 AUTOMATIC all wheel drive 4 Luxury Midsize Wagon 20 16 3105 2000 Audi 100 1992 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1992 regular unleaded 172 6 MANUAL all wheel drive 4 Luxury Midsize Sedan 21 16 3105 2000 Audi 100 1993 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1993 regular unleaded 172 6 AUTOMATIC all wheel drive 4 Luxury Midsize Wagon 20 16 3105 2000 Audi 100 1993 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1993 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1993 regular unleaded 172 6 MANUAL all wheel drive 4 Luxury Midsize Sedan 21 16 3105 2000 Audi 100 1994 regular unleaded 172 6 AUTOMATIC front wheel drive 4 Luxury Midsize Wagon 21 16 3105 2000 Audi 100 1994 regular unleaded 172 6 MANUAL all wheel drive 4 Luxury Midsize Sedan 22 16 3105 2000 Audi 100 1994 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 22 17 3105 2000 Audi 100 1994 regular unleaded 172 6 AUTOMATIC front wheel drive 4 Luxury Midsize Sedan 22 16 3105 2000 Audi 100 1994 regular unleaded 172 6 AUTOMATIC all wheel drive 4 Luxury Midsize Wagon 21 16 3105 2000 BMW 2 Series 2016 premium unleaded (required) 240 4 AUTOMATIC rear wheel drive 2 Luxury,Performance Compact Coupe 35 23 3916

Brand Model Year Fuel_Type Horsepower Cylinders Transmission Drive_Type Doors Category Size Style MPG_Highway MPG_City Popularity Price

Brand Model Year Fuel_Type Horsepower Cylinders Transmission Drive_Type Doors Category Size Style MPG_Highway MPG_City Popularity Price BMW 1 Series M 2011 premium unleaded (required) 335 6 MANUAL rear wheel drive 2 Factory Tuner,Luxury,High-Performance Compact Coupe 26 19 3916 46135 BMW 1 Series 2011 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 28 19 3916 40650 BMW 1 Series 2011 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 36350 BMW 1 Series 2011 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 18 3916 29450 BMW 1 Series 2011 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 18 3916 34500 BMW 1 Series 2012 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 18 3916 31200 BMW 1 Series 2012 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 26 17 3916 44100 BMW 1 Series 2012 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 39300 BMW 1 Series 2012 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 18 3916 36900 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 27 18 3916 37200 BMW 1 Series 2013 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 39600 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 19 3916 31500 BMW 1 Series 2013 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 28 19 3916 44400 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 19 3916 37200 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 19 3916 31500 BMW 1 Series 2013 premium unleaded (required) 320 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Convertible 25 18 3916 48250 BMW 1 Series 2013 premium unleaded (required) 320 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 43550 FIAT 124 Spider 2017 premium unleaded (recommended) 160 4 MANUAL rear wheel drive 2 Performance Compact Convertible 35 26 819 27495 FIAT 124 Spider 2017 premium unleaded (recommended) 160 4 MANUAL rear wheel drive 2 Performance Compact Convertible 35 26 819 24995 FIAT 124 Spider 2017 premium unleaded (recommended) 160 4 MANUAL rear wheel drive 2 Performance Compact Convertible 35 26 819 28195 BMW 2 Series 2016 premium unleaded (required) 240 4 AUTOMATIC rear wheel drive 2 Luxury,Performance Compact Coupe 35 23 3916 32850 BMW 2 Series 2016 premium unleaded (required) 240 4 AUTOMATIC rear wheel drive 2 Luxury Compact Convertible 34 23 3916 38650 BMW 2 Series 2016 premium unleaded (required) 320 6 AUTOMATIC rear wheel drive 2 Factory Tuner,Luxury,High-Performance Compact Convertible 31 20 3916 48750 BMW 2 Series 2016 premium unleaded (required) 240 4 AUTOMATIC all wheel drive 2 Luxury,Performance Compact Coupe 35 23 3916 34850 BMW 2 Series 2016 premium unleaded (required) 240 4 AUTOMATIC all wheel drive 2 Luxury Compact Convertible 34 22 3916 40650 BMW 2 Series 2016 premium unleaded (required) 320 6 AUTOMATIC rear wheel drive 2 Factory Tuner,Luxury,High-Performance Compact Coupe 31 20 3916 44150 BMW 2 Series 2016 premium unleaded (required) 240 4 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 34 22 3916 32850 BMW 2 Series 2016 premium unleaded (required) 320 6 AUTOMATIC all wheel drive 2 Factory Tuner,Luxury,High-Performance Compact Coupe 30 20 3916 46150 BMW 2 Series 2016 premium unleaded (required) 320 6 AUTOMATIC rear wheel drive 2 Factory Tuner,Luxury,High-Performance Compact Convertible 30 20 3916 507

Brand Model Year Fuel_Type Horsepower Cylinders Transmission Drive_Type Doors Category Size Style MPG_Highway MPG_City Popularity Price BMW 1 Series 2011 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 28 19 3916 40650 BMW 1 Series 2011 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 18 3916 34500 BMW 1 Series 2012 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 26 17 3916 44100 BMW 1 Series 2012 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 18 3916 36900 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 27 18 3916 37200 BMW 1 Series 2013 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 28 19 3916 44400 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 19 3916 37200 BMW 1 Series 2013 premium unleaded (required) 320 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Convertible 25 18 3916 48250 FIAT 124 Spider 2017 premium unleaded (recommended) 160 4 MANUAL rear wheel drive 2 Performance Compact Convertible 35 26 819 27495 FIAT 124 Spider 2017 premium unleaded (recommended) 160 4 MANUAL rear wheel drive 2 Performance Compact Convertible 35 26 819 24995 FIAT 124 Spider 2017 premium unleaded (recommended) 160 4 MANUAL rear wheel drive 2 Performance Compact Convertible 35 26 819 28195 BMW 2 Series 2016 premium unleaded (required) 240 4 AUTOMATIC rear wheel drive 2 Luxury Compact Convertible 34 23 3916 38650 BMW 2 Series 2016 premium unleaded (required) 320 6 AUTOMATIC rear wheel drive 2 Factory Tuner,Luxury,High-Performance Compact Convertible 31 20 3916 48750 BMW 2 Series 2016 premium unleaded (required) 240 4 AUTOMATIC all wheel drive 2 Luxury Compact Convertible 34 22 3916 40650 BMW 2 Series 2016 premium unleaded (required) 320 6 AUTOMATIC rear wheel drive 2 Factory Tuner,Luxury,High-Performance Compact Convertible 30 20 3916 50750 BMW 2 Series 2017 premium unleaded (recommended) 335 6 AUTOMATIC rear wheel drive 2 Factory Tuner,Luxury,High-Performance Compact Convertible 32 21 3916 49050 BMW 2 Series 2017 premium unleaded (recommended) 335 6 AUTOMATIC all wheel drive 2 Factory Tuner,Luxury,High-Performance Compact Convertible 32 21 3916 51050 BMW 2 Series 2017 premium unleaded (recommended) 248 4 AUTOMATIC rear wheel drive 2 Luxury,Performance Compact Convertible 34 23 3916 38950 BMW 2 Series 2017 premium unleaded (recommended) 248 4 AUTOMATIC all wheel drive 2 Luxury Compact Convertible 33 23 3916 40950 Mercedes-Benz 300-Class 1991 regular unleaded 228 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 21 14 617 3552 Mercedes-Benz 300-Class 1992 regular unleaded 228 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 21 15 617 3814 Mercedes-Benz 300-Class 1993 regular unleaded 228 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 21 14 617 4174 Nissan 300ZX 1994 regular unleaded 222 6 MANUAL rear wheel drive 2 Performance Compact Convertible 22 16 2009 2847 Nissan 300ZX 1995 regular unleaded 222 6 MANUAL rear wheel drive 2 Performance Compact Convertible 22 17 2009 3101 Nissan 300ZX 1996 regular unleaded 222 6 MANUAL rear wheel drive 2 Performance Compact Convertible 22 17 2009 3624 Nissan 350Z 2007 regular unleaded 306 6 AUTOMATIC rear wheel drive 2 High-Performance Compact Convertible 23 17 2009 36550 Nissan 350Z 2007 regular unleaded 306 6 AUTOMATIC rear wheel drive 2 High-Performance Compact Convertible 23 17 2009 41250 Nissan 350Z 2007 regular unleaded 306 6 MANUAL rear wheel drive 2 High-Performance Compact Convertible 24 17 2009 40250 Nissan 350Z 2007 regular unleaded 306 6 MANUAL rear wheel drive 2 High-Performance Compact Convertible 24 17 2009 35550 Nissan 350Z 2007 regular unleaded 306 6 MANUAL rear wheel drive 2 H

Brand Model Year Fuel_Type Horsepower Cylinders Transmission Drive_Type Doors Category Size Style MPG_Highway MPG_City Popularity Price Audi 100 1992 regular unleaded 172 6 AUTOMATIC all wheel drive 4 Luxury Midsize Wagon 20 16 3105 2000 Audi 100 1992 regular unleaded 172 6 MANUAL all wheel drive 4 Luxury Midsize Sedan 21 16 3105 2000 Audi 100 1993 regular unleaded 172 6 AUTOMATIC all wheel drive 4 Luxury Midsize Wagon 20 16 3105 2000 Audi 100 1993 regular unleaded 172 6 MANUAL all wheel drive 4 Luxury Midsize Sedan 21 16 3105 2000 Audi 100 1994 regular unleaded 172 6 MANUAL all wheel drive 4 Luxury Midsize Sedan 22 16 3105 2000 Audi 100 1994 regular unleaded 172 6 AUTOMATIC all wheel drive 4 Luxury Midsize Wagon 21 16 3105 2000 BMW 2 Series 2016 premium unleaded (required) 240 4 AUTOMATIC all wheel drive 2 Luxury,Performance Compact Coupe 35 23 3916 34850 BMW 2 Series 2016 premium unleaded (required) 240 4 AUTOMATIC all wheel drive 2 Luxury Compact Convertible 34 22 3916 40650 BMW 2 Series 2016 premium unleaded (required) 320 6 AUTOMATIC all wheel drive 2 Factory Tuner,Luxury,High-Performance Compact Coupe 30 20 3916 46150 BMW 2 Series 2017 premium unleaded (recommended) 335 6 AUTOMATIC all wheel drive 2 Factory Tuner,Luxury,High-Performance Compact Coupe 31 21 3916 46450 BMW 2 Series 2017 premium unleaded (recommended) 335 6 AUTOMATIC all wheel drive 2 Factory Tuner,Luxury,High-Performance Compact Convertible 32 21 3916 51050 BMW 2 Series 2017 premium unleaded (recommended) 248 4 AUTOMATIC all wheel drive 2 Luxury,Performance Compact Coupe 33 24 3916 35150 BMW 2 Series 2017 premium unleaded (recommended) 248 4 AUTOMATIC all wheel drive 2 Luxury Compact Convertible 33 23 3916 40950 Audi 200 1990 regular unleaded 162 5 MANUAL all wheel drive 4 Luxury Midsize Wagon 22 15 3105 2000 Audi 200 1990 regular unleaded 162 5 MANUAL all wheel drive 4 Luxury Midsize Sedan 23 15 3105 2000 Audi 200 1991 regular unleaded 217 5 MANUAL all wheel drive 4 Luxury,Performance Midsize Sedan 22 16 3105 2000 Audi 200 1991 regular unleaded 217 5 MANUAL all wheel drive 4 Luxury,Performance Midsize Wagon 22 16 3105 2000 Chrysler 200 2015 flex-fuel (unleaded/E85) 295 6 AUTOMATIC all wheel drive 4 Flex Fuel,Performance Midsize Sedan 29 18 1013 29370 Chrysler 200 2015 flex-fuel (unleaded/E85) 295 6 AUTOMATIC all wheel drive 4 Flex Fuel,Performance Midsize Sedan 29 18 1013 30825 Chrysler 200 2016 flex-fuel (unleaded/E85) 295 6 AUTOMATIC all wheel drive 4 Flex Fuel,Performance Midsize Sedan 29 18 1013 31785 Chrysler 200 2016 flex-fuel (unleaded/E85) 295 6 AUTOMATIC all wheel drive 4 Flex Fuel,Performance Midsize Sedan 29 18 1013 29905 Chrysler 200 2017 flex-fuel (unleaded/E85) 295 6 AUTOMATIC all wheel drive 4 Flex Fuel,Performance Midsize Sedan 28 18 1013 29905 Chrysler 200 2017 flex-fuel (unleaded/E85) 295 6 AUTOMATIC all wheel drive 4 Flex Fuel,Performance Midsize Sedan 28 18 1013 31785 Chrysler 200 2017 flex-fuel (unleaded/E85) 295 6 AUTOMATIC all wheel drive 4 Flex Fuel,Performance Midsize Sedan 28 18 1013 30900 BMW 3 Series Gran Turismo 2015 premium unleaded (required) 300 6 AUTOMATIC all wheel drive 4 Hatchback,Luxury,Performance Midsize 4dr Hatchback 30 20 3916 47250 BMW 3 Series Gran Turismo 2015 premium unleaded (required) 240 4 AUTOMATIC all wheel drive 4 Hatchback,Luxury Midsize 4dr Hatchback 33 22 3916 41850 BMW 3 Series Gran Turismo 2015 premium unleaded (required) 240 4 AUTOMATIC all wheel drive 4 Hatchback,Luxury Midsize 4dr Hatchback 33 22 3916 41850 BMW 3 Series Gran Turismo 2016 premium unleaded (required) 240 4 AUTOMATIC all wheel drive 4 Hatchback,Luxury Midsize 4dr Hatchback 34 22 3916 43000 BMW 3 Series Gran Turismo 2016 premium unleaded (required) 300 6 AUTOMATIC all wheel drive 4 Hatchback,Luxury,Performance Midsize 4dr Hatchback 30 20 3916 49200 BMW 3 Series Gran Turismo 2017 premium unleaded (required) 320 6 AUTOMATIC all wheel drive 4 Hatchback,Luxury,Performance Midsize 4dr Hatchback 30 20 3916 49650 BMW 3 Series Gran Turismo 20

In [0]:
display(df.select('Brand').distinct())

Brand Volkswagen Oldsmobile Infiniti Lexus FIAT Maserati Rolls-Royce Scion Mitsubishi Kia Chevrolet Volvo Hyundai Saab Honda Audi Lamborghini Cadillac Plymouth Genesis Pontiac Land Rover Alfa Romeo Mercedes-Benz McLaren Chrysler Lincoln Tesla BMW Suzuki Acura HUMMER Ferrari GMC Buick Porsche Spyker Lotus Bentley Toyota Aston Martin Dodge Nissan Mazda Maybach Ford Subaru Bugatti

In [0]:
#User Defined Function - Brand Name and Country Of Make 

def CountryMake(Brand):
  if Brand=='Volkswagen' or Brand=='Audi' or Brand=='Mercedes-Benz' or Brand=='BMW' or Brand=='Porsche' or Brand=='Maybach':
    return 'Germany'
  
  elif Brand=='Oldsmobile' or Brand=='Scion' or Brand=='Chevrolet' or Brand=='Plymouth' or Brand=='Cadillac' or Brand=='Pontiac':
    return 'USA'
  
  elif Brand=='Buick' or Brand=='Ford':
    return 'USA'

  elif Brand=='Chrysler' or Brand=='Lincoln' or Brand=='Tesla' or Brand=='HUMMER' or Brand=='Accura' or Brand=='GMC' or Brand=='Dodge':
    return 'USA'
  
  elif Brand=='Infiniti' or Brand=='Lexus' or Brand=='Mitsubishi' or Brand=='Honda' or Brand=='Suzuki' or Brand=='Toyota' or Brand=='Nissan':
    return 'Japan'
  
  elif Brand=='Mazda':
    return 'Japan'
  
  elif Brand=='FIAT' or Brand=='Maserati' or Brand=='Lamborghini' or Brand=='Alfa Romeo' or Brand=='Ferrari':
    return 'Italy'
  
  elif Brand=='Rolls-Royce' or Brand=='McLaren' or Brand=='Lotus' or Brand=='Bentley' or Brand=='Aston Martin':
    return 'UK'
  
  elif Brand=='Kia' or Brand=='Hyundai' or Brand=='Genesis':
    return 'South Korea'
  
  elif Brand=='Volvo' or Brand=='Saab':
    return 'Sweden'
  
  elif Brand=='Land Rover':
    return 'India'
   
  elif Brand=='Spyker':
    return 'Netherlands'
  
  elif Brand=='Bugatti':
    return 'France'
  
  else:
    return 'Other'  

In [0]:
#Register as a UDF- (User Defined Function)

spark.udf.register("Country",CountryMake)

Out[298]: <function __main__.CountryMake(Brand)>

In [0]:
#Create Table as Views for Running SQL Queries (as a Hive Table- Lazy Evaluation)

df.createOrReplaceTempView("Auto_Data")

In [0]:
#Querying SQL Data using SparkSQL - Testing Our UDF

display(spark.sql("SELECT Brand,Country(Brand) from Auto_Data"))

Brand Country(Brand) BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany Audi Germany Audi Germany Audi Germany Audi Germany Audi Germany Audi Germany Audi Germany Audi Germany Audi Germany Audi Germany Audi Germany Audi Germany Audi Germany Audi Germany Audi Germany FIAT Italy FIAT Italy FIAT Italy Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany Audi Germany Audi Germany Audi Germany Audi Germany Audi Germany Audi Germany Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Volvo Sweden Volvo Sweden Volvo Sweden Volvo Sweden Volvo Sweden Volvo Sweden Volvo Sweden Volvo Sweden Mazda Japan Mazda Japan Mazda Japan Mazda Japan Mazda Japan Mazda Japan Mazda Japan Mazda Japan Mazda Japan Mazda Japan Mazda Japan Mazda Japan BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany BMW Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mitsubishi Japan Mitsubishi Japan Mitsubishi Japan Mitsubishi Japan Mitsubishi Japan Mitsubishi Japan Mitsubishi Japan Mitsubishi Japan Mitsubishi Japan Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Chrysler USA Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Mazda Japan Mazda Japan Mazda Japan Mazda Japan Mazda Japan Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Mercedes-Benz Germany Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Nissan Japan Ferrari Italy Ferrari Italy Ferrari Italy Ferrari Italy Ferrari Italy Ferrari Italy Ferrari Italy Ferrari Italy Ferrari Italy Ferrari Italy Ferrari Italy Ferrari Italy Ferrari Italy Nissan Japan Nissan Japan Nissan Japa

In [0]:
# Window Functions in Spark 

windowSpec=Window.partitionBy(df['Brand']).orderBy(df['Price'])

car_prices=df.withColumn('On Road Price',max('Price').over(windowSpec))
            
display(car_prices.select('Brand','Model','Year','Fuel_Type','Transmission','Drive_Type','MPG_Highway','MPG_City','On Road Price').dropDuplicates())

Brand Model Year Fuel_Type Transmission Drive_Type MPG_Highway MPG_City On Road Price Acura Legend 1993 regular unleaded MANUAL front wheel drive 23 15 2000 Acura Legend 1993 regular unleaded MANUAL front wheel drive 23 16 2000 Acura Vigor 1992 regular unleaded MANUAL front wheel drive 24 18 2000 Acura Vigor 1993 regular unleaded MANUAL front wheel drive 24 18 2000 Acura Vigor 1994 regular unleaded MANUAL front wheel drive 24 18 2000 Acura Legend 1994 regular unleaded MANUAL front wheel drive 23 16 2028 Acura Legend 1993 regular unleaded MANUAL front wheel drive 23 15 2042 Acura Legend 1993 regular unleaded MANUAL front wheel drive 23 16 2060 Acura Legend 1994 regular unleaded AUTOMATIC front wheel drive 22 17 2063 Acura Legend 1994 regular unleaded MANUAL front wheel drive 24 16 2066 Acura Legend 1995 regular unleaded MANUAL front wheel drive 24 16 2066 Acura Legend 1995 regular unleaded MANUAL front wheel drive 23 16 2135 Acura Legend 1995 regular unleaded AUTOMATIC front wheel drive 22 17 2144 Acura Legend 1994 regular unleaded MANUAL front wheel drive 24 16 2181 Acura Legend 1995 regular unleaded MANUAL front wheel drive 24 16 2265 Acura Legend 1995 regular unleaded AUTOMATIC front wheel drive 22 17 2356 Acura Legend 1994 regular unleaded MANUAL front wheel drive 24 16 2384 Acura SLX 1997 regular unleaded AUTOMATIC four wheel drive 17 13 2397 Acura SLX 1997 regular unleaded AUTOMATIC four wheel drive 17 13 2488 Acura Legend 1995 regular unleaded MANUAL front wheel drive 24 16 2506 Acura Integra 1999 regular unleaded MANUAL front wheel drive 29 22 2799 Acura SLX 1998 regular unleaded AUTOMATIC four wheel drive 18 13 2816 Acura Integra 1999 regular unleaded MANUAL front wheel drive 29 22 2827 Acura Integra 1999 regular unleaded MANUAL front wheel drive 29 22 2912 Acura SLX 1999 regular unleaded AUTOMATIC four wheel drive 18 13 2934 Acura Integra 1999 regular unleaded MANUAL front wheel drive 29 22 3000 Acura Integra 2000 regular unleaded MANUAL front wheel drive 28 22 3012 Acura Integra 2000 regular unleaded MANUAL front wheel drive 28 22 3086 Acura Integra 2000 regular unleaded MANUAL front wheel drive 28 22 3130 Acura Integra 2000 regular unleaded MANUAL front wheel drive 28 22 3222 Acura Integra 1999 regular unleaded MANUAL front wheel drive 28 22 3355 Acura Integra 1999 regular unleaded MANUAL front wheel drive 28 22 3381 Acura Integra 2000 regular unleaded MANUAL front wheel drive 28 22 3622 Acura Integra 2000 regular unleaded MANUAL front wheel drive 28 22 3652 Acura Integra 2000 regular unleaded MANUAL front wheel drive 28 22 7398 Acura Integra 2001 regular unleaded MANUAL front wheel drive 28 22 19400 Acura RSX 2004 regular unleaded MANUAL front wheel drive 30 24 20025 Acura Integra 2001 regular unleaded AUTOMATIC front wheel drive 28 21 20200 Acura Integra 2001 regular unleaded MANUAL front wheel drive 28 22 20200 Acura RSX 2005 regular unleaded MANUAL front wheel drive 31 24 20275 Acura RSX 2006 regular unleaded MANUAL front wheel drive 31 24 20325 Acura RSX 2004 regular unleaded AUTOMATIC front wheel drive 31 22 20925 Acura Integra 2001 regular unleaded AUTOMATIC front wheel drive 28 21 21000 Acura Integra 2001 regular unleaded MANUAL front wheel drive 28 22 21050 Acura RSX 2004 regular unleaded MANUAL front wheel drive 30 24 21100 Acura RSX 2005 regular unleaded AUTOMATIC front wheel drive 31 22 21175 Acura RSX 2006 regular unleaded AUTOMATIC front wheel drive 31 22 21225 Acura RSX 2005 regular unleaded MANUAL front wheel drive 31 24 21350 Acura RSX 2006 regular unleaded MANUAL front wheel drive 31 24 21475 Acura Integra 2001 regular unleaded MANUAL front wheel drive 28 22 21600 Acura Integra 2001 regular unleaded AUTOMATIC front wheel drive 28 21 21850 Acura RSX 2004 regular unleaded AUTOMATIC front wheel drive 31 22 22000 Acura RSX 2005 regular unleaded AUTOMATIC front wheel drive 31 22 22250 Acura Integra 2001 premium unleaded (required) MANUAL front wheel drive 28 22 22300 Acura RSX 2006 regular unleaded AUTO

In [0]:
#SQL Queries 

display(spark.sql("SELECT Brand,Model,Year,Drive_Type,Price FROM Auto_Data WHERE Transmission='AUTOMATED_MANUAL' OR Fuel_Type='premium unleaded (required)'"))

Brand Model Year Drive_Type Price BMW 1 Series M 2011 rear wheel drive 46135 BMW 1 Series 2011 rear wheel drive 40650 BMW 1 Series 2011 rear wheel drive 36350 BMW 1 Series 2011 rear wheel drive 29450 BMW 1 Series 2011 rear wheel drive 34500 BMW 1 Series 2012 rear wheel drive 31200 BMW 1 Series 2012 rear wheel drive 44100 BMW 1 Series 2012 rear wheel drive 39300 BMW 1 Series 2012 rear wheel drive 36900 BMW 1 Series 2013 rear wheel drive 37200 BMW 1 Series 2013 rear wheel drive 39600 BMW 1 Series 2013 rear wheel drive 31500 BMW 1 Series 2013 rear wheel drive 44400 BMW 1 Series 2013 rear wheel drive 37200 BMW 1 Series 2013 rear wheel drive 31500 BMW 1 Series 2013 rear wheel drive 48250 BMW 1 Series 2013 rear wheel drive 43550 BMW 2 Series 2016 rear wheel drive 32850 BMW 2 Series 2016 rear wheel drive 38650 BMW 2 Series 2016 rear wheel drive 48750 BMW 2 Series 2016 all wheel drive 34850 BMW 2 Series 2016 all wheel drive 40650 BMW 2 Series 2016 rear wheel drive 44150 BMW 2 Series 2016 rear wheel drive 32850 BMW 2 Series 2016 all wheel drive 46150 BMW 2 Series 2016 rear wheel drive 50750 BMW 3 Series Gran Turismo 2015 all wheel drive 47250 BMW 3 Series Gran Turismo 2015 all wheel drive 41850 BMW 3 Series Gran Turismo 2015 all wheel drive 41850 BMW 3 Series Gran Turismo 2016 all wheel drive 43000 BMW 3 Series Gran Turismo 2016 all wheel drive 49200 BMW 3 Series Gran Turismo 2017 all wheel drive 49650 BMW 3 Series Gran Turismo 2017 all wheel drive 43950 BMW 3 Series 2015 all wheel drive 41950 BMW 3 Series 2015 rear wheel drive 50150 BMW 3 Series 2015 rear wheel drive 37500 BMW 3 Series 2015 rear wheel drive 43750 BMW 3 Series 2015 all wheel drive 39500 BMW 3 Series 2015 all wheel drive 39500 BMW 3 Series 2015 all wheel drive 34950 BMW 3 Series 2015 all wheel drive 45750 BMW 3 Series 2015 rear wheel drive 37500 BMW 3 Series 2015 rear wheel drive 32950 BMW 3 Series 2016 all wheel drive 47800 BMW 3 Series 2016 rear wheel drive 38350 BMW 3 Series 2016 all wheel drive 40350 BMW 3 Series 2016 rear wheel drive 38350 BMW 3 Series 2016 all wheel drive 42650 BMW 3 Series 2016 rear wheel drive 33150 BMW 3 Series 2016 all wheel drive 35150 BMW 3 Series 2016 rear wheel drive 45800 Chrysler 300M 2002 front wheel drive 32065 Chrysler 300M 2002 front wheel drive 28540 Chrysler 300M 2003 front wheel drive 32315 Chrysler 300M 2004 front wheel drive 32615 Ferrari 360 2002 rear wheel drive 160829 Ferrari 360 2002 rear wheel drive 140615 Ferrari 360 2002 rear wheel drive 150694 Ferrari 360 2002 rear wheel drive 170829 Ferrari 360 2003 rear wheel drive 165986 Ferrari 360 2003 rear wheel drive 154090 Ferrari 360 2003 rear wheel drive 143860 Ferrari 360 2003 rear wheel drive 176287 Ferrari 360 2004 rear wheel drive 157767 Ferrari 360 2004 rear wheel drive 187124 Ferrari 360 2004 rear wheel drive 147332 Ferrari 360 2004 rear wheel drive 169900 Ferrari 360 2004 rear wheel drive 180408 Nissan 370Z 2015 rear wheel drive 46790 Nissan 370Z 2015 rear wheel drive 48100 Nissan 370Z 2015 rear wheel drive 29990 Nissan 370Z 2015 rear wheel drive 41820 Nissan 370Z 2015 rear wheel drive 31290 Nissan 370Z 2015 rear wheel drive 34870 Nissan 370Z 2015 rear wheel drive 33570 Nissan 370Z 2015 rear wheel drive 46570 Nissan 370Z 2015 rear wheel drive 37970 Nissan 370Z 2015 rear wheel drive 37070 Nissan 370Z 2015 rear wheel drive 49400 Nissan 370Z 2015 rear wheel drive 45270 Nissan 370Z 2015 rear wheel drive 39270 Nissan 370Z 2015 rear wheel drive 45490 Nissan 370Z 2015 rear wheel drive 41990 Nissan 370Z 2015 rear wheel drive 38370 Nissan 370Z 2015 rear wheel drive 43290 Nissan 370Z 2016 rear wheel drive 41820 Nissan 370Z 2016 rear wheel drive 48100 Nissan 370Z 2016 rear wheel drive 43290 Nissan 370Z 2016 rear wheel drive 39270 Nissan 370Z 2016 rear wheel drive 34870 Nissan 370Z 2016 rear wheel drive 41990 Nissan 370Z 2016 rear wheel drive 38370 Nissan 370Z 2016 rear wheel drive 45270 Nissan 370Z 2016 rear wheel drive 45490 Nissan 370Z 2016 rear wheel drive 29990 Nissan 370Z 2016

In [0]:
display(spark.sql("SELECT * from Auto_Data"))

Brand Model Year Fuel_Type Horsepower Cylinders Transmission Drive_Type Doors Category Size Style MPG_Highway MPG_City Popularity Price BMW 1 Series M 2011 premium unleaded (required) 335 6 MANUAL rear wheel drive 2 Factory Tuner,Luxury,High-Performance Compact Coupe 26 19 3916 46135 BMW 1 Series 2011 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 28 19 3916 40650 BMW 1 Series 2011 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 36350 BMW 1 Series 2011 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 18 3916 29450 BMW 1 Series 2011 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 18 3916 34500 BMW 1 Series 2012 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 18 3916 31200 BMW 1 Series 2012 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 26 17 3916 44100 BMW 1 Series 2012 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 39300 BMW 1 Series 2012 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 18 3916 36900 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 27 18 3916 37200 BMW 1 Series 2013 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 39600 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 19 3916 31500 BMW 1 Series 2013 premium unleaded (required) 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 28 19 3916 44400 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 19 3916 37200 BMW 1 Series 2013 premium unleaded (required) 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 19 3916 31500 BMW 1 Series 2013 premium unleaded (required) 320 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Convertible 25 18 3916 48250 BMW 1 Series 2013 premium unleaded (required) 320 6 MANUAL rear wheel drive 2 Luxury,High-Performance Compact Coupe 28 20 3916 43550 Audi 100 1992 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1992 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1992 regular unleaded 172 6 AUTOMATIC all wheel drive 4 Luxury Midsize Wagon 20 16 3105 2000 Audi 100 1992 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1992 regular unleaded 172 6 MANUAL all wheel drive 4 Luxury Midsize Sedan 21 16 3105 2000 Audi 100 1993 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1993 regular unleaded 172 6 AUTOMATIC all wheel drive 4 Luxury Midsize Wagon 20 16 3105 2000 Audi 100 1993 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1993 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 Audi 100 1993 regular unleaded 172 6 MANUAL all wheel drive 4 Luxury Midsize Sedan 21 16 3105 2000 Audi 100 1994 regular unleaded 172 6 AUTOMATIC front wheel drive 4 Luxury Midsize Wagon 21 16 3105 2000 Audi 100 1994 regular unleaded 172 6 MANUAL all wheel drive 4 Luxury Midsize Sedan 22 16 3105 2000 Audi 100 1994 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 22 17 3105 2000 Audi 100 1994 regular unleaded 172 6 AUTOMATIC front wheel drive 4 Luxury Midsize Sedan 22 16 3105 2000 Audi 100 1994 regular unleaded 172 6 AUTOMATIC all wheel drive 4 Luxury Midsize Wagon 21 16 3105 2000 FIAT 124 Spider 2017 premium unleaded (recommended) 160 4 MANUAL rear wheel drive 2 Performance Compact Convertible 35 26 81

In [0]:
df.cache()

Out[304]:

Brand Model Year Fuel_Type Horsepower Cylinders Transmission Drive_Type Doors Category Size Style MPG_Highway MPG_City Popularity Price 
 BMW 1 Series M 2011 premium unleaded ... 335 6 MANUAL rear wheel drive 2 Factory Tuner,Lux... Compact Coupe 26 19 3916 46135 
 BMW 1 Series 2011 premium unleaded ... 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 28 19 3916 40650 
 BMW 1 Series 2011 premium unleaded ... 300 6 MANUAL rear wheel drive 2 Luxury,High-Perfo... Compact Coupe 28 20 3916 36350 
 BMW 1 Series 2011 premium unleaded ... 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 18 3916 29450 
 BMW 1 Series 2011 premium unleaded ... 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 18 3916 34500 
 BMW 1 Series 2012 premium unleaded ... 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 18 3916 31200 
 BMW 1 Series 2012 premium unleaded ... 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 26 17 3916 44100 
 BMW 1 Series 2012 premium unleaded ... 300 6 MANUAL rear wheel drive 2 Luxury,High-Perfo... Compact Coupe 28 20 3916 39300 
 BMW 1 Series 2012 premium unleaded ... 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 18 3916 36900 
 BMW 1 Series 2013 premium unleaded ... 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 27 18 3916 37200 
 BMW 1 Series 2013 premium unleaded ... 300 6 MANUAL rear wheel drive 2 Luxury,High-Perfo... Compact Coupe 28 20 3916 39600 
 BMW 1 Series 2013 premium unleaded ... 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 19 3916 31500 
 BMW 1 Series 2013 premium unleaded ... 300 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Convertible 28 19 3916 44400 
 BMW 1 Series 2013 premium unleaded ... 230 6 MANUAL rear wheel drive 2 Luxury Compact Convertible 28 19 3916 37200 
 BMW 1 Series 2013 premium unleaded ... 230 6 MANUAL rear wheel drive 2 Luxury,Performance Compact Coupe 28 19 3916 31500 
 BMW 1 Series 2013 premium unleaded ... 320 6 MANUAL rear wheel drive 2 Luxury,High-Perfo... Compact Convertible 25 18 3916 48250 
 BMW 1 Series 2013 premium unleaded ... 320 6 MANUAL rear wheel drive 2 Luxury,High-Perfo... Compact Coupe 28 20 3916 43550 
 Audi 100 1992 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 
 Audi 100 1992 regular unleaded 172 6 MANUAL front wheel drive 4 Luxury Midsize Sedan 24 17 3105 2000 
 Audi 100 1992 regular unleaded 172 6 AUTOMATIC all wheel drive 4 Luxury Midsize Wagon 20 16 3105 2000 
 
only showing top 20 rows

In [0]:
#Write Data to CSV 

#Write Data to CSV File in DBFS - Append Mode 

#Other Modes are - overwrite,ignore.

df.write.format("csv").mode("append").save("/FileStore/tables/output/results.csv")